In [3]:
import ROOT
import glob
import math
import numpy as np
from IPython.display import display, Markdown
from IPython.display import display, HTML
from TPCQCVis.src.drawHistograms import *
from TPCQCVis.src.drawTrending import *
from TPCQCVis.src.checkHistograms import *

In [4]:
display(HTML("<style>.container { width:90% !important; }</style>"))
display(HTML("<style>table {float:left;}</style>"))

In [5]:
# Read the Root Files
path = "/home/berki/alice/data/asyncQC/LHC22f/apass1/"
fileList = glob.glob(path+"*_QC.root")
fileList.sort()
runList = [fileList[i][52:-8] for i in range(len(fileList))]
rootDataFile=[]
for file in fileList:
    rootDataFile.append(ROOT.TFile.Open(file,"READ"))
#rootDataFile[0].ls()
#rootDataFile[0].ClusterQC.ls()
#rootDataFile[0].PIDQC.ls()
#rootDataFile[0].TracksQC.ls()
#runList

# Reporting on TPC QC for LHC22f
> 13.6 TeV pp <br />
> Link to JIRA: https://alice.its.cern.ch/jira/browse/O2-3127 <br />
> B = +0.5 T <br />
> beam = pp <br />
> energy (sqrt) = 13.6 TeV <br />

+ Runs:
 + 520259
 + 520265
 + 520271
 + 520282
 + 520283
 + 520288
 + 520290
 + 520294
 + 520296
 + 520297
 + 520471
 + 520472

## General comments
+ A side phi distribution not flat
+ Reduced high pT tail and number_of_cluster distribution on last two runs (520471, 520472) with higher colliding bcs

---
## Number of recorded tracks per run
+ Looking at hPt histogram from tracks task
+ With cuts (nClusters > 60, |eta| < 1, dEdxTot > 20)

In [6]:
%jsroot on
objectName="hPt;1"
[trend,canvas] = drawTrending(objectName,rootDataFile,names=runList,trend="entries",error="",log="logy",namesFromRunList=True)
canvas.Draw()

---
## Tracks QC
**Notes:** Runs `OK`

## Phi distribution of tracks:

+ General:
 + Sector boundaries much more prominent compared to earlier runs.
 
+ RUN 523142:
 + Promblem in Sector A7
+ RUN 523148:
 + Problem in Sectors A0 & A1

In [7]:
%jsroot on
objectName="hPhiAside"
[hist,legend,canvas,pad1] = drawHistograms(objectName,rootDataFile,normalize=True,legend=True,legendNames=runList,pads=False, drawOption="SAME L")

#Sector boundatries
pad1.cd()
sectorBoundary = ROOT.TLine(0,hist.GetMinimum(),0,hist.GetMaximum())
sectorBoundary.SetLineStyle(2)
sectorNum = ROOT.TText(.5,.5,"test")
sectorNum.SetTextAlign(22)
sectorNum.SetTextColor(ROOT.kGray+1)
sectorNum.SetTextFont(0)
for j in range(19):
    sectorBoundary.DrawLine((j*2*math.pi)/18,hist.GetMinimum(),(j*2*math.pi)/18,hist.GetMaximum())
    if j < 18 : sectorNum.DrawText(((j+0.5)*2*math.pi)/18,hist.GetMaximum(),str(j))
    
canvas.Draw()

+ C-side no major issues observed

In [8]:
%jsroot on
objectName="hPhiCside"
[hist,legend,canvas,pad1] = drawHistograms(objectName,rootDataFile,normalize=True,legend=True,legendNames=runList,pads=False, drawOption="SAME L")
#Sector boundatries
pad1.cd()
sectorBoundary = ROOT.TLine(0,hist.GetMinimum(),0,hist.GetMaximum())
sectorBoundary.SetLineStyle(2)
sectorNum = ROOT.TText(.5,.5,"test")
sectorNum.SetTextAlign(22)
sectorNum.SetTextColor(ROOT.kGray+1)
sectorNum.SetTextFont(0)
for j in range(19):
    sectorBoundary.DrawLine((j*2*math.pi)/18,hist.GetMinimum(),(j*2*math.pi)/18,hist.GetMaximum())
    if j < 18 : sectorNum.DrawText(((j+0.5)*2*math.pi)/18,hist.GetMaximum(),str(j))
        
canvas.Draw()

### Number of clusters vs phi

In [9]:
%jsroot on
objectName="h2DNClustersPhiAside"
[hist,legend,canvas,pad1] = drawHistograms(objectName,rootDataFile[0:4],normalize=False,legend=False,legendNames=runList[0:4],pads=True,drawOption="COLZ")
canvas.Draw()

In [10]:
%jsroot on
objectName="h2DNClustersPhiCside"
[hist,legend,canvas,pad1] = drawHistograms(objectName,rootDataFile[0:4],normalize=False,legend=False,legendNames=runList[0:4],pads=True,drawOption="COLZ")
canvas.Draw()

---
### Pt distribution

+ All runs similar, no differences in high-pt tails observed
+ Result: `OK`

In [9]:
%jsroot on
objectName="hPt"
[hist,legend,canvas,pad1] = drawHistograms(objectName,rootDataFile,normalize=True,legend=True,log="logxy",legendNames=runList,pads=False)
canvas.Draw()

---
### Clusters per track

+ Main peak is broader compared to previous runs
+ Secondary peak also prominent

In [10]:
%jsroot on
objectName="hNClustersAfterCuts"
[hist,legend,canvas,pad1] = drawHistograms(objectName,rootDataFile,normalize=True,legend=True,legendNames=runList,pads=False)
canvas.Draw()

### Number of clusters vs eta
+ cluster distrubution not flat over eta especially for negative eta (C-side)
+ Result: `BAD`

In [11]:
%jsroot on
objectName="h2DNClustersEta"
[hist,legend,canvas,pad1] = drawHistograms(objectName,rootDataFile,normalize=False,legend=False,legendNames=runList,pads=True,drawOption="COLZ")
canvas.Draw()

---
### Sign of tracks

+ Ratio of pos/neg tracks consistent in all runs

In [12]:
%jsroot on
objectName="hSign"
[hist,legend,canvas,pad1] = drawHistograms(objectName,rootDataFile,normalize=True,legend=True,legendNames=runList,pads=False)
canvas.Draw()

---
## PID QC

### MIP signal
+ No major outliers observed, all MIP peaks at ~50
 + All **GOOD**

In [13]:
%jsroot on
objectName="hdEdxTotMIP_TPC"
quality = checkHistograms(objectName,rootDataFile,check="(histogram.Fit(\"gaus\",\"Sq\",\"\",40,60)) and 45<histogram.GetFunction(\"gaus\").GetParameter(1)<55")
[hist,legend,canvas,pad1] = drawHistograms(objectName,rootDataFile,legendNames=runList,check=quality,normalize=False,log="logx",legend=False,pads=True)
canvas.Draw()

---
### dEdx vs P
+ No unexpected shapes observed
+ All **GOOD**

In [14]:
%jsroot on
objectName="hdEdxTotVsP_TPC"
[hist,legend,canvas,pad1] = drawHistograms(objectName,rootDataFile,legendNames=runList,log="logxz",pads=True,drawOption="COLZ")
canvas.Draw()